# Xử lý Dữ liệu cho Visual Question Answering (VQA)

Notebook này chứa các đoạn code để xử lý bộ dữ liệu MS COCO VQA. Quy trình bao gồm:
1. Phân tích cấu trúc các file JSON
2. Gộp dữ liệu câu hỏi và annotations
3. Đổi tên các file hình ảnh
4. Gộp các file chunk đã được dịch
5. Lọc hình ảnh dựa trên dữ liệu JSON
6. Chuyển đổi giữa định dạng JSONL và JSON
7. Gộp dữ liệu cuối cùng với nhận diện ngôn ngữ

In [4]:
import json

## 1. Import Thư viện JSON

Import thư viện cần thiết để làm việc với các file JSON.

In [ ]:


def print_structure(data, indent=0):
    prefix = "  " * indent
    if isinstance(data, dict):
        for key, value in data.items():
            print(f"{prefix}{key}: {type(value).__name__}")
            print_structure(value, indent + 1)
    elif isinstance(data, list):
        if data:
            # In thông tin phần tử đầu tiên của list để minh họa cấu trúc
            print(f"{prefix}[List of {type(data[0]).__name__} (chỉ xem phần tử đầu tiên)]")
            print_structure(data[0], indent + 1)
        else:
            print(f"{prefix}[Empty list]")
    else:
        # Nếu là kiểu dữ liệu cơ bản (int, str, etc.) thì in ra giá trị (bạn có thể bỏ qua nếu chỉ cần type)
        print(f"{prefix}{data} (type: {type(data).__name__})")

# Danh sách các file bạn cần phân tích cấu trúc
files = [
    "v2_mscoco_val2014_annotations.json",
    "v2_mscoco_val2014_complementary_pairs.json",
    "v2_OpenEnded_mscoco_val2014_questions.json"
]

for file in files:
    print(f"\nCấu trúc của file {file}:")
    try:
        with open(file, 'r') as f:
            data = json.load(f)
        print_structure(data)
    except Exception as e:
        print(f"Không thể mở hoặc xử lý file {file}: {e}")



Cấu trúc của file v2_mscoco_val2014_annotations.json:
info: dict
  description: str
    This is v2.0 of the VQA dataset. (type: str)
  url: str
    http://visualqa.org (type: str)
  version: str
    2.0 (type: str)
  year: int
    2017 (type: int)
  contributor: str
    VQA Team (type: str)
  date_created: str
    2017-04-26 17:00:44 (type: str)
license: dict
  url: str
    http://creativecommons.org/licenses/by/4.0/ (type: str)
  name: str
    Creative Commons Attribution 4.0 International License (type: str)
data_subtype: str
  val2014 (type: str)
annotations: list
  [List of dict (chỉ xem phần tử đầu tiên)]
    question_type: str
      none of the above (type: str)
    multiple_choice_answer: str
      down (type: str)
    answers: list
      [List of dict (chỉ xem phần tử đầu tiên)]
        answer: str
          down (type: str)
        answer_confidence: str
          yes (type: str)
        answer_id: int
          1 (type: int)
    image_id: int
      262148 (type: int)
    ans

## 2. Phân tích Cấu trúc File JSON

Cell này định nghĩa một hàm đệ quy để phân tích và in ra cấu trúc của các file JSON. Giúp hiểu định dạng dữ liệu của bộ dữ liệu MS COCO VQA:

**Chức năng chính:**
- **`print_structure()`**: Duyệt đệ quy qua dữ liệu JSON và in ra cấu trúc
- Xử lý dictionary, list và các kiểu dữ liệu cơ bản
- Chỉ hiển thị phần tử đầu tiên của list để tránh xuất ra quá nhiều thông tin
- Phân tích 3 file quan trọng:
  - `v2_mscoco_val2014_annotations.json` - Chứa câu trả lời và annotations
  - `v2_mscoco_val2014_complementary_pairs.json` - Chứa các cặp question ID
  - `v2_OpenEnded_mscoco_val2014_questions.json` - Chứa các câu hỏi

**Ý nghĩa:** Đây là bước quan trọng để hiểu cấu trúc dữ liệu trước khi xử lý.

In [2]:
import json

# Hàm load dữ liệu từ file JSON
def load_json(filename):
    with open(filename, 'r') as f:
        return json.load(f)

# Load dữ liệu từ 3 file
annotations_data = load_json("v2_mscoco_val2014_annotations.json")
questions_data = load_json("v2_OpenEnded_mscoco_val2014_questions.json")
pairs_data = load_json("v2_mscoco_val2014_complementary_pairs.json")

# Tạo dictionary mapping cho annotation và question theo question_id
# Trong annotations, mỗi phần tử có khóa "question_id"
annotations_dict = {item["question_id"]: item for item in annotations_data["annotations"]}

# Trong questions, mỗi phần tử có khóa "question_id"
questions_dict = {item["question_id"]: item for item in questions_data["questions"]}

# Danh sách chứa các phần tử đã merge
merged_list = []

# Duyệt qua từng group trong pairs_data (giả sử mỗi group là list các question_id)
for group in pairs_data:
    for qid in group:
        # Kiểm tra tồn tại của qid ở cả annotations và questions
        if qid in questions_dict and qid in annotations_dict:
            q_item = questions_dict[qid]
            a_item = annotations_dict[qid]
            merged_item = {
                "question": q_item["question"],
                "answer": a_item["multiple_choice_answer"],
                "image_id": q_item["image_id"]
            }
            merged_list.append(merged_item)
        else:
            print(f"Warning: question_id {qid} không tìm thấy trong cả 2 file.")

# Ghi kết quả ra file JSON mới
with open("merged_data.json", "w") as f:
    json.dump(merged_list, f, indent=2)

print("Đã tạo file merged_data.json với", len(merged_list), "phần tử.")


Đã tạo file merged_data.json với 190288 phần tử.


## 3. Gộp Dữ liệu Câu hỏi và Annotations

Cell này gộp dữ liệu từ 3 file JSON để tạo ra một dataset thống nhất:

**Quy trình:**
1. **Load dữ liệu** từ 3 file JSON
2. **Tạo dictionary** để tra cứu nhanh theo `question_id`
3. **Duyệt qua các cặp** trong file complementary pairs
4. **Gộp các record khớp** có tồn tại trong cả file questions và annotations
5. **Trích xuất các trường cần thiết**:
   - `question` từ file questions
   - `answer` từ file annotations (multiple_choice_answer)
   - `image_id` để liên kết với hình ảnh

**Kết quả:** Tạo ra file `merged_data.json` với các cặp câu hỏi-trả lời được đơn giản hóa và liên kết với image ID.

**Ý nghĩa:** Bước này rất quan trọng để tạo ra định dạng dataset VQA sạch và dễ sử dụng.

In [3]:
import os
import re

# Đường dẫn tới thư mục chứa các file hình (nếu file nằm trong thư mục khác, thay đổi đường dẫn tại đây)
directory = '/home/fuc/Documents/DataWorkSpace/Computer_Vision/Final/Data/val2014'

# Biểu thức chính quy để trích xuất số từ tên file
pattern = re.compile(r"COCO_val2014_0*(\d+)\.jpg")

# Duyệt qua từng file trong thư mục
for filename in os.listdir(directory):
    match = pattern.match(filename)
    if match:
        image_id = match.group(1)  # Lấy phần id (số)
        new_name = f"{image_id}.jpg"
        old_path = os.path.join(directory, filename)
        new_path = os.path.join(directory, new_name)
        print(f"Đổi tên {filename} -> {new_name}")
        os.rename(old_path, new_path)

print("Đã đổi tên tất cả các file hình.")


Đổi tên COCO_val2014_000000141597.jpg -> 141597.jpg
Đổi tên COCO_val2014_000000486360.jpg -> 486360.jpg
Đổi tên COCO_val2014_000000286353.jpg -> 286353.jpg
Đổi tên COCO_val2014_000000064116.jpg -> 64116.jpg
Đổi tên COCO_val2014_000000071385.jpg -> 71385.jpg
Đổi tên COCO_val2014_000000220111.jpg -> 220111.jpg
Đổi tên COCO_val2014_000000160025.jpg -> 160025.jpg
Đổi tên COCO_val2014_000000075234.jpg -> 75234.jpg
Đổi tên COCO_val2014_000000496618.jpg -> 496618.jpg
Đổi tên COCO_val2014_000000284282.jpg -> 284282.jpg
Đổi tên COCO_val2014_000000316147.jpg -> 316147.jpg
Đổi tên COCO_val2014_000000493867.jpg -> 493867.jpg
Đổi tên COCO_val2014_000000322887.jpg -> 322887.jpg
Đổi tên COCO_val2014_000000322503.jpg -> 322503.jpg
Đổi tên COCO_val2014_000000310669.jpg -> 310669.jpg
Đổi tên COCO_val2014_000000084097.jpg -> 84097.jpg
Đổi tên COCO_val2014_000000385641.jpg -> 385641.jpg
Đổi tên COCO_val2014_000000498971.jpg -> 498971.jpg
Đổi tên COCO_val2014_000000334021.jpg -> 334021.jpg
Đổi tên COCO_val

## 4. Đổi Tên File Hình Ảnh

Cell này chuẩn hóa tên file hình ảnh bằng cách loại bỏ tiền tố COCO:

**Mục đích:** 
- Chuyển đổi từ `COCO_val2014_000000123456.jpg` thành `123456.jpg`
- Giúp dễ dàng khớp file hình với `image_id` trong dữ liệu JSON

**Quy trình:**
1. Sử dụng regex pattern để trích xuất ID số từ tên file COCO
2. Loại bỏ các số 0 ở đầu từ ID được trích xuất
3. Đổi tên file chỉ sử dụng ID số

**Regex Pattern:** `COCO_val2014_0*(\d+)\.jpg`
- Khớp với tiền tố COCO
- Bắt phần số (loại bỏ số 0 ở đầu)
- Đảm bảo có đuôi .jpg

**Ý nghĩa:** Đơn giản hóa quá trình khớp hình ảnh với dữ liệu trong các bước sau.

In [1]:
import json
import glob
import os

def merge_json_files(input_folder, output_file):
    merged_data = []
    # Lấy danh sách các file có dạng chunk_*.json trong thư mục input_folder
    file_pattern = os.path.join(input_folder, "chunk_*.json")
    json_files = glob.glob(file_pattern)
    
    # Duyệt từng file và gộp dữ liệu
    for file in json_files:
        with open(file, 'r', encoding='utf-8') as f:
            data = json.load(f)
            merged_data.extend(data)
    
    # Ghi dữ liệu đã gộp vào file đầu ra
    with open(output_file, 'w', encoding='utf-8') as f:
        json.dump(merged_data, f, ensure_ascii=False, indent=2)
    
    print(f"Đã gộp {len(json_files)} file thành file {output_file}")
    print(f"Tổng số dòng dữ liệu trong file output: {len(merged_data)}")

if __name__ == "__main__":
    input_folder = "translated_chunks"  # Thư mục chứa các file chunk_*.json
    output_file = "output_merged_data.json"     # File đầu ra sau khi gộp
    merge_json_files(input_folder, output_file)


Đã gộp 1902 file thành file output_merged_data.json
Tổng số dòng dữ liệu trong file output: 190188


## 5. Gộp Các File JSON Chunk

Cell này kết hợp nhiều file JSON chunk thành một file duy nhất:

**Trường hợp sử dụng:** Khi dữ liệu đã được chia thành nhiều chunk (ví dụ: để xử lý song song hoặc dịch thuật)

**Quy trình:**
1. **Tìm tất cả file chunk** khớp với pattern `chunk_*.json` trong thư mục chỉ định
2. **Load và kết hợp** tất cả dữ liệu JSON từ các file này
3. **Lưu dữ liệu đã gộp** vào một file output duy nhất

**Tính năng:**
- Sử dụng `glob` để tìm file khớp với pattern
- Mở rộng danh sách merged với dữ liệu từ mỗi chunk
- Bảo toàn encoding UTF-8 cho các ký tự quốc tế
- Báo cáo số lượng file đã gộp và tổng số record

**Cấu hình:**
- Thư mục input: `translated_chunks`
- File output: `output_merged_data.json`

**Ý nghĩa:** Thường được sử dụng sau các thao tác dịch thuật hoặc xử lý batch khác.

In [2]:
import os
import json
import shutil

def filter_images(json_file, images_folder, output_folder):
    # Đọc file JSON đã gộp
    with open(json_file, 'r', encoding='utf-8') as f:
        data = json.load(f)
    
    # Lấy danh sách các image_id có trong file JSON
    image_ids = set(record["image_id"] for record in data)
    print(f"Tìm thấy {len(image_ids)} image_id trong file JSON.")
    
    # Tạo thư mục chứa ảnh đã lọc nếu chưa tồn tại
    os.makedirs(output_folder, exist_ok=True)
    
    copied_count = 0
    skipped_count = 0
    # Duyệt qua tất cả các ảnh trong folder images_folder
    for image_file in os.listdir(images_folder):
        name, ext = os.path.splitext(image_file)
        if ext.lower() not in ['.jpg', '.jpeg', '.png']:
            continue  # Bỏ qua các file không phải ảnh
        
        if name.isdigit() and int(name) in image_ids:
            src_path = os.path.join(images_folder, image_file)
            dst_path = os.path.join(output_folder, image_file)
            # Nếu file đã tồn tại trong folder đích thì bỏ qua
            if os.path.exists(dst_path):
                skipped_count += 1
                print(f"Bỏ qua {image_file} (đã tồn tại)")
                continue
            
            shutil.copy(src_path, dst_path)
            copied_count += 1
            print(f"Đã copy {image_file}")
    
    print(f"Đã copy {copied_count} ảnh mới, bỏ qua {skipped_count} ảnh đã tồn tại.")

def count_images_in_folder(folder_path):
    image_count = 0
    image_extensions = {'.jpg', '.jpeg', '.png'}
    
    for filename in os.listdir(folder_path):
        if os.path.splitext(filename)[1].lower() in image_extensions:
            image_count += 1
    
    return image_count

if __name__ == "__main__":
    json_file = "output_merged_data.json"
    images_folder = "val2014"
    output_folder = "filtered_images"
    
    # Đếm số ảnh trong folder mới
    total_images = count_images_in_folder(output_folder)
    print(f"Tổng số ảnh trong folder {output_folder}: {total_images}")
    
    # Chạy hàm filter nếu cần
    filter_images(json_file, images_folder, output_folder)

Tổng số ảnh trong folder filtered_images: 36264
Tìm thấy 40170 image_id trong file JSON.
Đã copy 504439.jpg
Bỏ qua 151956.jpg (đã tồn tại)
Bỏ qua 281929.jpg (đã tồn tại)
Bỏ qua 91372.jpg (đã tồn tại)
Bỏ qua 257537.jpg (đã tồn tại)
Bỏ qua 509262.jpg (đã tồn tại)
Đã copy 80104.jpg
Bỏ qua 390238.jpg (đã tồn tại)
Đã copy 80096.jpg
Bỏ qua 197280.jpg (đã tồn tại)
Bỏ qua 365866.jpg (đã tồn tại)
Bỏ qua 185393.jpg (đã tồn tại)
Bỏ qua 51355.jpg (đã tồn tại)
Bỏ qua 211674.jpg (đã tồn tại)
Bỏ qua 353148.jpg (đã tồn tại)
Bỏ qua 125673.jpg (đã tồn tại)
Bỏ qua 350075.jpg (đã tồn tại)
Bỏ qua 455937.jpg (đã tồn tại)
Bỏ qua 325587.jpg (đã tồn tại)
Đã copy 286524.jpg
Bỏ qua 65860.jpg (đã tồn tại)
Bỏ qua 14380.jpg (đã tồn tại)
Bỏ qua 441553.jpg (đã tồn tại)
Bỏ qua 212761.jpg (đã tồn tại)
Bỏ qua 441483.jpg (đã tồn tại)
Bỏ qua 273645.jpg (đã tồn tại)
Đã copy 289222.jpg
Bỏ qua 502927.jpg (đã tồn tại)
Bỏ qua 251768.jpg (đã tồn tại)
Bỏ qua 435444.jpg (đã tồn tại)
Bỏ qua 216419.jpg (đã tồn tại)
Bỏ qua 85940.jpg

## 6. Lọc Hình Ảnh Dựa Trên Dữ Liệu JSON

Cell này lọc các file hình ảnh để chỉ giữ lại những hình được tham chiếu trong dữ liệu JSON:

**Mục đích:** 
- Giảm kích thước dataset bằng cách chỉ giữ hình ảnh liên quan
- Đảm bảo tính nhất quán giữa file hình và record JSON

**Hàm chính:**

### `filter_images()`
1. **Đọc file JSON** và trích xuất tất cả giá trị `image_id` duy nhất
2. **Tạo thư mục output** nếu chưa tồn tại
3. **Copy hình ảnh khớp** từ thư mục nguồn đến thư mục đích
4. **Bỏ qua file đã tồn tại** để tránh trùng lặp
5. **Báo cáo tiến trình** và thống kê

### `count_images_in_folder()`
- Đếm file hình (.jpg, .jpeg, .png) trong một thư mục
- Sử dụng để kiểm tra và báo cáo

**Workflow:**
1. Đếm hình ảnh hiện có trong thư mục output
2. Chạy quá trình lọc
3. Chỉ copy những hình có tên file số khớp với `image_id` trong JSON

**Cấu hình:**
- File JSON: `output_merged_data.json`
- Thư mục nguồn: `val2014`
- Thư mục đích: `filtered_images`

**Ý nghĩa:** Tối ưu hóa lưu trữ và đảm bảo tính nhất quán dữ liệu.

In [5]:
def convert_jsonl_to_json(jsonl_file, json_file):
    with open(jsonl_file, 'r', encoding='utf-8') as f_in:
        data = [json.loads(line) for line in f_in]
    with open(json_file, 'w', encoding='utf-8') as f_out:
        json.dump(data, f_out, ensure_ascii=False, indent=4)
    print(f"Đã chuyển từ {jsonl_file} sang {json_file}")

# Gọi sau khi hoàn thành
convert_jsonl_to_json("output_merged_data_fixed.jsonl", "output_merged_data_fixed.json")

Đã chuyển từ output_merged_data_fixed.jsonl sang output_merged_data_fixed.json


## 7. Chuyển Đổi Định Dạng JSONL Sang JSON

Cell này chuyển đổi định dạng JSONL (JSON Lines) sang định dạng JSON chuẩn:

**JSONL vs JSON:**
- **JSONL**: Mỗi dòng là một JSON object riêng biệt (định dạng streaming)
- **JSON**: Một JSON array duy nhất chứa tất cả object (định dạng chuẩn)

**Quy trình:**
1. **Đọc file JSONL** từng dòng một
2. **Parse mỗi dòng** thành JSON object
3. **Kết hợp thành list** chứa tất cả object
4. **Ghi ra JSON chuẩn** với định dạng đẹp

**Tính năng:**
- Bảo toàn encoding UTF-8
- In đẹp với indentation
- Xử lý encoding đúng cách cho văn bản quốc tế

**Ví dụ sử dụng:**
- Input: `output_merged_data_fixed.jsonl`
- Output: `output_merged_data_fixed.json`

**Ý nghĩa:** Chuyển đổi này hữu ích khi cần định dạng JSON chuẩn để tương thích với các công cụ khác.

In [1]:
import json
import os
import concurrent.futures
from langdetect import detect
from tqdm import tqdm

# Đường dẫn file
ORIGINAL_FILE = "output_merged_data.json"
FIXED_FILE = "output_merged_data_fixed.jsonl"
OUTPUT_MERGED_FILE = "output_merged_data_final.json"
CHUNK_SIZE = 1000  # Kích thước mỗi chunk để xử lý song song

# Hàm kiểm tra xem văn bản có phải tiếng Việt không
def is_vietnamese(text):
    try:
        return detect(text) == 'vi'
    except:
        return False

# Hàm đọc file JSONL thành danh sách
def read_jsonl(file_path):
    data = []
    if os.path.exists(file_path):
        with open(file_path, 'r', encoding='utf-8') as f:
            for line in f:
                if line.strip():
                    data.append(json.loads(line))
    return data

# Hàm gộp dữ liệu cho một chunk
def merge_chunk(chunk, fixed_dict):
    merged_chunk = []
    for orig_item in chunk:
        image_id = orig_item["image_id"]
        fixed_item = fixed_dict.get(image_id)
        if fixed_item and is_vietnamese(fixed_item["question"]) and is_vietnamese(fixed_item["answer"]):
            merged_chunk.append(fixed_item)
        else:
            merged_chunk.append(orig_item)
    return merged_chunk

# Hàm gộp dữ liệu chính với đa luồng
def merge_data(original_data, fixed_data):
    fixed_dict = {item["image_id"]: item for item in fixed_data}
    merged_data = []

    # Chia dữ liệu thành các chunk
    chunks = [original_data[i:i + CHUNK_SIZE] for i in range(0, len(original_data), CHUNK_SIZE)]
    
    # Sử dụng ThreadPoolExecutor để xử lý song song
    with concurrent.futures.ThreadPoolExecutor(max_workers=8) as executor:
        futures = {executor.submit(merge_chunk, chunk, fixed_dict): i for i, chunk in enumerate(chunks)}
        
        # Dùng tqdm để hiển thị tiến trình
        for future in tqdm(concurrent.futures.as_completed(futures), total=len(chunks), desc="Merging chunks"):
            chunk_result = future.result()
            merged_data.extend(chunk_result)

    # Sắp xếp lại theo thứ tự ban đầu (nếu cần)
    merged_data.sort(key=lambda x: x["image_id"])
    return merged_data

def main():
    # Đọc dữ liệu từ file gốc
    with open(ORIGINAL_FILE, 'r', encoding='utf-8') as f:
        original_data = json.load(f)
    print(f"Tổng số phần tử trong {ORIGINAL_FILE}: {len(original_data)}")

    # Đọc dữ liệu từ file fixed
    fixed_data = read_jsonl(FIXED_FILE)
    print(f"Tổng số phần tử trong {FIXED_FILE}: {len(fixed_data)}")

    # Gộp dữ liệu với đa luồng
    merged_data = merge_data(original_data, fixed_data)
    print(f"Tổng số phần tử sau khi gộp: {len(merged_data)}")

    # Lưu file kết quả
    with open(OUTPUT_MERGED_FILE, 'w', encoding='utf-8') as f:
        json.dump(merged_data, f, ensure_ascii=False, indent=4)
    print(f"Đã gộp và lưu vào {OUTPUT_MERGED_FILE}")

if __name__ == "__main__":
    main()

Tổng số phần tử trong output_merged_data.json: 190188
Tổng số phần tử trong output_merged_data_fixed.jsonl: 143788


Merging chunks: 100%|██████████| 191/191 [06:38<00:00,  2.09s/it]


Tổng số phần tử sau khi gộp: 190188
Đã gộp và lưu vào output_merged_data_final.json


## 8. Gộp Dữ Liệu Nâng Cao Với Nhận Diện Ngôn Ngữ

Cell này thực hiện gộp dữ liệu phức tạp với nhận diện ngôn ngữ và xử lý song song:

**Mục đích:** 
- Gộp dữ liệu tiếng Anh gốc với dữ liệu đã dịch sang tiếng Việt
- Sử dụng bản dịch tiếng Việt khi có sẵn và hợp lệ
- Fallback về dữ liệu gốc khi bản dịch thiếu hoặc không hợp lệ

**Tính năng chính:**

### Nhận Diện Ngôn Ngữ
- **`is_vietnamese()`**: Sử dụng thư viện `langdetect` để nhận diện văn bản tiếng Việt
- Xử lý lỗi nhận diện một cách graceful

### Xử Lý Song Song
- **`merge_chunk()`**: Xử lý chunk dữ liệu song song
- **`ThreadPoolExecutor`**: Sử dụng 8 worker để xử lý đồng thời
- **Theo dõi tiến trình**: Sử dụng `tqdm` để hiển thị tiến trình trực quan

### Logic Gộp Thông Minh
1. **Load cả 2 dataset**: Gốc và đã sửa/dịch
2. **Tạo lookup dictionary** từ dữ liệu fixed theo `image_id`
3. **Xử lý theo chunk** để tiết kiệm bộ nhớ
4. **Chọn phiên bản tốt nhất**: Tiếng Việt nếu có và hợp lệ, nếu không thì dùng gốc
5. **Sắp xếp theo image_id** để duy trì thứ tự nhất quán

**Cấu hình:**
- File gốc: `output_merged_data.json`
- File fixed/dịch: `output_merged_data_fixed.jsonl`
- File output: `output_merged_data_final.json`
- Kích thước chunk: 1000 record mỗi chunk
- Max workers: 8 threads

**Lợi ích về hiệu suất:**
- Xử lý song song giảm thời gian thực thi
- Xử lý theo chunk xử lý hiệu quả dataset lớn
- Theo dõi tiến trình cung cấp phản hồi cho người dùng

**Ý nghĩa:** Tạo ra dataset cuối cùng chất lượng cao với các bản dịch tốt nhất có sẵn.